In [ ]:
#@title Colab setup
import os, sys, subprocess
if "google.colab" in sys.modules:
  cmd = "pip install --upgrade biocircuits bokeh-catplot watermark blackcellmagic intersect"
  process = subprocess.Popen(cmd.split(), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
  stdout, stderr = process.communicate()
# ------

import scipy.integrate
import bokeh.io
import numpy as np
from intersect import intersection

import biocircuits
import numba

from skimage import measure
from intersect import intersection
import sympy as sp
import pylab as pl

import bokeh.io
import bokeh.plotting
import bokeh.palettes
from bokeh.models import LinearColorMapper, ColorBar
from bokeh.models import Range1d
from bokeh.io import export_svgs

bokeh.io.output_notebook()

In [ ]:
# Some auxiliary functions

def JoinMatrices(A,B):

  # Function to create two matrices of differense size by placing them in a diagonal [A, 0 ; 0, B]

  n1, m1 = A.shape
  n2, m2 = B.shape
  ZA = np.zeros((n1,m2))
  ZB = np.zeros((n2,m1))
  tmp1 = np.hstack((A,ZA))
  tmp2 = np.hstack((ZB,B))
  return np.vstack((tmp1,tmp2))

In [ ]:
#@title Negative and positive feedback with $u_1$ actuation

# ################################################################################
# ##################### NEGATIVE FEEDBACK WITH U1 ACTUATION ######################
# ################################################################################

def ODE_NF_u1(X, t, a, K, m, d, b, k, xi, th, g):
    """
    Right hand desribe production and degradation and return dx/dt
    """
    y1, y2, u1, u2, x = X

    return (
      [
          a * K**m / (K**m + y2**m) - d*y1 + b*u1, # d y1 / dt =
          a * K**m / (K**m + y1**m) - d*y2  , # d y1 / dt = # u2 stabilize
          k * x - d*u1 - g*u1*u2, # d u2 / dt =
          xi * K**m / (K**m + y1**m) - d*u2 - g*u1*u2, # d u2 / dt =
          th * K**m / (K**m + y1**m) - d*x, # d u2 / dt =
      ]
  )

# Nulcliness analysis
def Compute_IO(y, a, K, m, d, b, k, xi, th, g):
  x = th/d*K**m/(K**m + y**m)
  f1 = k*x
  f2 = xi*K**m/(K**m + y**m)

  A = (f2-f1)/d + d/g
  B = -f1/g

  u1 = 0.5*(-A + (A**2 - 4*B)**0.5)

  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m) # (1) Eq y1(y2) (hill + b*u1) / d
  y2_2 = a/d*K**m/(K**m + y**m)

  return (y2_1,y2_2, u1)

def Compute_IO_2(y, a, K, m, d, b, k, xi, th, g):
    x = th/d*K**m/(K**m + y**m)
    f1 = k*x
    f2 = xi*K**m/(K**m + y**m)

    A = (f2-f1)/d + d/g
    B = -f1/g

    u1 = 0.5*(-A + (A**2 - 4*B)**0.5)

    ym, tmp = intersection(y, a + b*u1, y, d*y)
    #print(ym)

    y1_1 = np.linspace(0,ym[0]*1.2,len(y))

    y2_2 = a/d*K**m/(K**m + y**m)

    return (y2_2, y1_1)

def Compute_IO_1(y, a, K, m, d, b, k, xi, th, g):
    x = th/d*K**m/(K**m + y**m)
    f1 = k*x
    f2 = xi*K**m/(K**m + y**m)

    A = (f2-f1)/d + d/g
    B = -f1/g

    u1 = 0.5*(-A + (A**2 - 4*B)**0.5)

    y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
    return (y2_1)

# Simple propensity function for Gillespie algorithm (stochastic)
def simple_propensity_NF_u1(propensities, population, t, a, K, m, d, b, k, xi, th, g, Omega):
    y1, y2, u1, u2, x = population
    # Toggle switch's equations
    propensities[0] = a * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # 0 -> Y1
    propensities[1] = d * y1 # Y1 -> 0
    propensities[2] = a * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # 0 -> Y1
    propensities[3] = d * y2 # Y2 -> 0
    propensities[4] = b * u1 # 0 -> Y1

    # Adaptive controller's equations
    propensities[5] = k * x # X -> X + U1
    propensities[6] = d * u1 # U1 -> 0
    propensities[7] = xi * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # Y1 -> Y1 + U2
    propensities[8] = d * u2 # U2 -> 0
    propensities[9] = th * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # Y1 -> Y1 + X
    propensities[10] = d * x # X -> 0
    propensities[11] = g * u1 * u2 / Omega # U1 + U2 -> 0

# ################################################################################
# ##################### POSITIVE FEEDBACK WITH U1 ACTUATION ######################
# ################################################################################

# Ordinary differential equations
def ODE_PF_u1(X, t, a, K, m, d, b, k, xi, th, g):
    """
    Right hand desribe production and degradation and return dx/dt
    """
    y1, y2, u1, u2, x = X

    return (
      [
          a * K**m / (K**m + y2**m) - d*y1 + b*u1, # d y1 / dt =
          a * K**m / (K**m + y1**m) - d*y2  , # d y1 / dt = # u2 stabilize
          k * x - d*u1 - g*u1*u2, # d u2 / dt =
          xi * K**m / (K**m + y2**m) - d*u2 - g*u1*u2, # d u2 / dt =
          th * K**m / (K**m + y2**m) - d*x, # d u2 / dt =
      ]
  )

# Nulcliness analysis
def PF_null_u1(y1_1, y2_2, a, K, m, d, b, k, xi, th, g):
  y2_1 = a/d * K**m / (K**m + y1_1**m)

  x = th/d * K**m / (K**m + y2_2**m)
  f1 = k*x
  f2 = xi * K**m / (K**m + y2_2**m)

  A = (f2-f1)/d + d/g
  B = -f1/g

  u1 = 0.5*(-A + (A**2 - 4*B)**0.5)

  y1_2 = (a/d) * K**m / (K**m + y2_2**m) + (b/d) * u1

  return (y2_1, y1_2)

# Simple propensity function
def simple_propensity_PF_u1(propensities, population, t, a, K, m, d, b, k, xi, th, g, Omega):
    y1, y2, u1, u2, x = population
    # Toggle switch's equations
    propensities[0] = a * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # 0 -> Y1
    propensities[1] = d * y1 # Y1 -> 0
    propensities[2] = a * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # 0 -> Y1
    propensities[3] = d * y2 # Y2 -> 0
    propensities[4] = b * u1 # 0 -> Y1

    # Adaptive controller's equations
    propensities[5] = k * x # X -> X + U1
    propensities[6] = d * u1 # U1 -> 0
    propensities[7] = xi * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # Y1 -> Y1 + U2
    propensities[8] = d * u2 # U2 -> 0
    propensities[9] = th * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # Y1 -> Y1 + X
    propensities[10] = d * x # X -> 0
    propensities[11] = g * u1 * u2 / Omega # U1 + U2 -> 0

# Changing the actuation of the adaptive controller.

Until now, we had been working with the negatived and positive feedback architectures whose effects were driven by the actuation of the $U_1$ species. In this simulation, we want to explore the structural symmetry of the controller and the effect of an actuation generated by the other species involved in the sequestration mechanism: $U_2$. In this case, the ODEs of the system will be modified as follows:

\begin{eqnarray}
  \frac{dy_1}{dt} &=& \alpha \frac{K^m}{K^m + y_2^m} - \delta y_1 + \beta u_2 \\
  \frac{dy_2}{dt} &=& \alpha \frac{K^m}{K^m + y_1^m} - \delta y_2 \\
\end{eqnarray}

On the other hand, the equations that describe the controller will remain the same.

\begin{eqnarray}
  \frac{du_1}{dt} = kx - \delta u_1 - \gamma u_1 u_2, \space \frac{du_2}{dt} = \xi \frac{K^m}{K^m + y_1^m} - \delta u_2 - \gamma u_1 u_2, \space  \frac{dx}{dt} = \theta \frac{K^m}{K^m + y_1^m} - \delta x
\end{eqnarray}

## Finding the steady state
\begin{eqnarray}
\bar y_1 &=& \sqrt[m]{\alpha \frac{K^m}{\delta \bar y_2} - K^m} \\
\bar y_2 &=& \sqrt[m]{\frac{\alpha K^m}{\delta \bar y_1 - \beta \bar u_2} - K^m}
\end{eqnarray}

In this case, We need to find $\bar u_2$ as a function of $\bar y_n$, where $n = \{1,2\}$
\begin{eqnarray}
\bar u_1 &=& \frac{f_2 - \delta \bar u_2}{\gamma \bar u_2} = \frac{f_1}{\delta + \gamma \bar u_2},
\end{eqnarray}

where $f_1 = k \bar x$, $f_2 = \xi \frac{K^m}{K^m + \bar y_x^m}$, and $\bar x = \frac{\theta}{\delta} \frac{K^m}{K^m + \bar y_x^m}$.

This leads to a second order polynomial, $P(\bar u_2) = \bar u_2^2 + A \bar u_2 + B = 0$, and leads to a single positive real solution
\begin{eqnarray}
\bar u_2 &= \frac{-A + \sqrt{A^2 - 4B}}{2}
\end{eqnarray}
where $A = \frac{f_1-f_2}{\delta} + \frac{\delta}{\gamma}$, and $B = - \frac{f_2}{\gamma}$.




In [ ]:
#@title Negative and positive feedback with $u_2$ actuation

# ##################################################################
# ####################### POSITIVE FEEDBACK ########################
# ##################################################################

def ODE_PF_u2(X, t, a, K, m, d, b, k, xi, th, g):

  y1, y2, u1, u2, x = X

  return (
      [
          a * K**m / (K**m + y2**m) - d*y1 + b*u2, # d y1 / dt =
          a * K**m / (K**m + y1**m) - d*y2  , # d y1 / dt =
          k * x - d*u1 - g*u1*u2, # d u2 / dt =
          xi * K**m / (K**m + y1**m) - d*u2 - g*u1*u2, # d u2 / dt =
          th * K**m / (K**m + y1**m) - d*x, # d u2 / dt =
      ]
  )

# Nullclines analysis
def PF_null_u2(y, a, K, m, d, b, k, xi, th, g):
  x = th/d*K**m/(K**m + y**m)
  f1 = k*x
  f2 = xi*K**m/(K**m + y**m)

  A = (f1-f2)/d + d/g
  B = -f2/g

  u2 = 0.5*(-A + (A**2 - 4*B)**0.5)

  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
  y2_2 = a/d*K**m/(K**m + y**m)

  return (y2_1,y2_2, u2)

def Compute_IO_2_u2(y, a, K, m, d, b, k, xi, th, g):
    x = th/d*K**m/(K**m + y**m)
    f1 = k*x
    f2 = xi*K**m/(K**m + y**m)

    A = (f1-f2)/d + d/g
    B = -f2/g

    u2 = 0.5*(-A + (A**2 - 4*B)**0.5)

    ym, tmp = intersection(y, a + b*u2, y, d*y)
    #print(ym)

    y1_1 = np.linspace(0,ym[0]*1.2,len(y))

    y2_2 = a/d*K**m/(K**m + y**m)

    return (y2_2, y1_1)

def Compute_IO_1_u2(y, a, K, m, d, b, k, xi, th, g):
    x = th/d*K**m/(K**m + y**m)
    f1 = k*x
    f2 = xi*K**m/(K**m + y**m)

    A = (f1-f2)/d + d/g
    B = -f2/g

    u2 = 0.5*(-A + (A**2 - 4*B)**0.5)

    y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
    return (y2_1)

def simple_propensity_PF_u2(propensities, population, t, a, K, m, d, b, k, xi, th, g, Omega):
    y1, y2, u1, u2, x = population
    # Toggle switch's equations
    propensities[0] = a * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # 0 -> Y1
    propensities[1] = d * y1 # Y1 -> 0
    propensities[2] = a * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # 0 -> Y1
    propensities[3] = d * y2 # Y2 -> 0
    propensities[4] = b * u2 # 0 -> Y1

    # Adaptive controller's equations
    propensities[5] = k * x # X -> X + U1
    propensities[6] = d * u1 # U1 -> 0
    propensities[7] = xi * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # Y1 -> Y1 + U2
    propensities[8] = d * u2 # U2 -> 0
    propensities[9] = th * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # Y1 -> Y1 + X
    propensities[10] = d * x # X -> 0
    propensities[11] = g * u1 * u2 / Omega # U1 + U2 -> 0

# ##################################################################
# ####################### NEGATIVE FEEDBACK ########################
# ##################################################################

def ODE_NF_u2(X, t, a, K, m, d, b, k, xi, th, g):
    """
    Right hand desribe production and degradation and return dx/dt
    """
    y1, y2, u1, u2, x = X

    return (
      [
          a * K**m / (K**m + y2**m) - d*y1 + b*u2, # d y1 / dt =
          a * K**m / (K**m + y1**m) - d*y2  , # d y1 / dt = # u2 stabilize
          k * x - d*u1 - g*u1*u2, # d u2 / dt =
          xi * K**m / (K**m + y2**m) - d*u2 - g*u1*u2, # d u2 / dt =
          th * K**m / (K**m + y2**m) - d*x, # d u2 / dt =
      ]
  )

# Nullclines analysis
def NF_null_u2(y1_1, y2_2, a, K, m, d, b, k, xi, th, g):

  x = th/d * K**m / (K**m + y1_1**m)
  f1 = k * x
  f2 = xi * K**m / (K**m + y1_1**m)

  A = (f1 - f2)/d + d/g
  B = - f2/g

  u2 = (-A + np.sqrt(A**2 - 4*B)) * 0.5

  y1_2 = a/d * K**m / (K**m + y2_2**m) + b/d * u2

  y2_1 = a/d * K**m / (K**m + y1_1**m)

  return (y1_2, y2_1)

def simple_propensity_NF_u2(propensities, population, t, a, K, m, d, b, k, xi, th, g, Omega):
    y1, y2, u1, u2, x = population
    # Switch 1 (Promoter pointing to the right R)
    propensities[0] = a * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # 0 -> Y1
    propensities[1] = d * y1 # Y1 -> 0
    propensities[2] = a * Omega * (K*Omega)**m/((K*Omega)**m + y1**m) # 0 -> Y1
    propensities[3] = d * y2 # Y2 -> 0
    propensities[4] = b * u2 # 0 -> Y1

    propensities[5] = k * x # X -> X + U1
    propensities[6] = d * u1 # U1 -> 0
    propensities[7] = xi * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # Y1 -> Y1 + U2
    propensities[8] = d * u2 # U2 -> 0
    propensities[9] = th * Omega * (K*Omega)**m/((K*Omega)**m + y2**m) # Y1 -> Y1 + X
    propensities[10] = d * x # X -> 0
    propensities[11] = g * u1 * u2 / Omega # U1 + U2 -> 0

# Stoichiometry  matrix of the toggle switch
# Y1, Y2
S1 = np.array(
    [
     [ 1, 0],  # 0 -> Y1
     [-1, 0],  # Y1 -> 0
     [ 0, 1],  # 0 -> Y2
     [ 0,-1],  # Y2 -> 0
     [ 1, 0],  # 0 -> Y1
    ],
    dtype=int,
)
#print(S1)

# Stoichiometry  matrix of the adaptive controller
# U1, U2, X
S2 = np.array(
    [
     [ 1, 0, 0], # X -> U1
     [-1, 0, 0], # U1 -> 0
     [ 0, 1, 0], # Y1 -> U2
     [ 0,-1, 0], # U2 -> 0
     [ 0, 0, 1], # Y1 -> X
     [ 0, 0,-1], # X -> 0
     [-1,-1, 0], # U1 + u2 -> 0
    ],
    dtype=int,
)
# Stoichiometry matrix of the closed loop system
simple_update = JoinMatrices(S1,S2)

## How does $u_2$ actuation affects the controller's dynamics?

In [ ]:
#@title Dynamics of the closed-loop system with $u_2$ actuation
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1
b = 3

# Time interval
t = np.linspace(0,20,400)

# Set up plots
fig_size = [320, 250] # to visualize

plots = []
for i in range(5):
    plots.append(bokeh.plotting.figure(width=fig_size[0], height=fig_size[1],
                          #x_range=x_range,y_range=y_range
                          x_axis_label = 't'),)
    plots[i].axis.major_label_text_font_size = "10pt"     #background_fill_color="#fafafa"

# Initial conditions
vecA = np.linspace(1,3,7)
vecB = np.ones(7)*2.9
vec_y1 = np.concatenate([vecB, vecA])
vec_y2 = np.concatenate([vecA, vecB])

# Without controller
args = (a, K, m, d, b*0, k, xi, th, g)

for ii in range(len(vec_y1)):

  x01 = np.array([vec_y1[ii] , vec_y2[ii] , 0., 0., 0.])

  # Solving the ODEs
  x1 = scipy.integrate.odeint(ODE_NF_u1, x01, t, args=args)
  x1 = x1.transpose()

  # Ploting
  plots[0].line(t,x1[0,:],line_width=2, color="black", legend_label = 'y1')
  plots[0].line(t,x1[1,:],line_width=2, color="orange", legend_label = 'y2')

plots[0].title.text = 'without controller'
plots[0].yaxis.axis_label = 'y'
plots[0].legend.background_fill_alpha = 0.00

# Positive feedback with u2 actuation
args = (a, K, m, d, b, k, xi, th, g)

for ii in range(len(vec_y1)):

  x01 = np.array([vec_y1[ii] , vec_y2[ii] , 0., 0., 0.])

  # Solving the ODEs
  x1 = scipy.integrate.odeint(ODE_PF_u2, x01, t, args=args)
  x1 = x1.transpose()

  # Ploting
  plots[1].line(t,x1[0,:],line_width=2, color="black", legend_label = 'y1')
  plots[1].line(t,x1[1,:],line_width=2, color="orange", legend_label = 'y2')

plots[1].title.text = 'Positive feedback with µ2 actuation'
plots[1].yaxis.axis_label = 'y'
plots[1].legend.background_fill_alpha = 0.00

# Negative feedback with u2 actuation
for ii in range(len(vec_y1)):

  x01 = np.array([vec_y1[ii] , vec_y2[ii] , 0., 0., 0.])

  # Solving the ODEs
  x1 = scipy.integrate.odeint(ODE_NF_u2, x01, t, args=args)
  x1 = x1.transpose()

  # Ploting
  plots[2].line(t,x1[0,:],line_width=2, color="black", legend_label = 'y1')
  plots[2].line(t,x1[1,:],line_width=2, color="orange", legend_label = 'y2')

plots[2].title.text = 'Negative feedback with µ2 actuation'
plots[2].yaxis.axis_label = 'y'
plots[2].legend.background_fill_alpha = 0.00

# Negative feedback with u1 actuation
for ii in range(len(vec_y1)):

  x01 = np.array([vec_y1[ii] , vec_y2[ii] , 0., 0., 0.])

  # Solving the ODEs
  x1 = scipy.integrate.odeint(ODE_NF_u1, x01, t, args=args)
  x1 = x1.transpose()

  # Ploting
  plots[3].line(t,x1[0,:],line_width=2, color="black", legend_label = 'y1')
  plots[3].line(t,x1[1,:],line_width=2, color="orange", legend_label = 'y2')

plots[3].title.text = 'Negative feedback with µ1 actuation'
plots[3].yaxis.axis_label = 'y'
plots[3].legend.background_fill_alpha = 0.00

# Positive feedback with u1 actuation
for ii in range(len(vec_y1)):

  x01 = np.array([vec_y1[ii] , vec_y2[ii] , 0., 0., 0.])

  # Solving the ODEs
  x1 = scipy.integrate.odeint(ODE_PF_u1, x01, t, args=args)
  x1 = x1.transpose()

  # Ploting
  plots[4].line(t,x1[0,:],line_width=2, color="black", legend_label = 'y1')
  plots[4].line(t,x1[1,:],line_width=2, color="orange", legend_label = 'y2')

plots[4].title.text = 'Positive feedback with µ1 actuation'
plots[4].yaxis.axis_label = 'y'
plots[4].legend.background_fill_alpha = 0.00

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([
    [plots[0], plots[1], plots[2]],
    [None, plots[3], plots[4]]
]))

In [ ]:
#@title Actuation through $u_2$ enables a biased output, too
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1
b = 1

Omega = 100 # 600

time_points = np.linspace(0, 20, 101)
population_0 = np.zeros(5, dtype=int)

# Parameters to analyze

args1 = (a, K, m, d, b*0, k, xi, th, g, Omega)
args2 = (a, K, m, d, b*3, k, xi, th, g, Omega)
args3 = (a, K, m, d, b*1, k, xi, th, g, Omega)

# Solving with Gillespie algorithm
samples1 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args1, n_threads=4,progress_bar=False)
samples2 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples3 = biocircuits.gillespie_ssa(simple_propensity_PF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples4 = biocircuits.gillespie_ssa(simple_propensity_NF_u2, simple_update, population_0,time_points, size=250, args=args3, n_threads=4,progress_bar=False)
samples5 = biocircuits.gillespie_ssa(simple_propensity_PF_u2, simple_update, population_0,time_points, size=250, args=args3, n_threads=4,progress_bar=False)

# Visualization
plots = []
for i in range(5):
  plots.append(bokeh.plotting.figure(width = 320, height = 225,
                                     x_range = (-300, 300), y_range = (0, 0.02),
                                     x_axis_label = 'y1 - y2', y_axis_label = 'p'))
# Reference plot
bin0 = np.arange(-3*Omega,3*Omega+6,8) #8
hist, bin_edges = np.histogram(samples1[:,-1,0] - samples1[:,-1,1], bin0, density=True)

plots[0].title.text = 'without controller'

for i in range(5):
  plots[i].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color="grey", line_color="grey", fill_alpha=0.2,line_alpha=0.)
  plots[i].step(bin_edges[:-1],hist, line_width=1, mode="after", color = "grey", legend_label = 'β = 0')
  plots[i].legend.location = 'top'
  plots[i].legend.background_fill_alpha = 0.0

# IFFL controllers
sample_vec = [samples2, samples3, samples4, samples5]
colors = ['orange', 'blue', 'purple', 'green']
labels = ['Negative feedback with µ1 actuation', 'Positive feedback with µ1 actuation',
          'Negative feedback with µ2 actuation', 'Positive feedback with µ2 actuation',]
tags = ['β = 3','β = 3', 'β = 1', 'β = 1']

for i, sample in enumerate(sample_vec):
  hist, bin_edges = np.histogram(sample[:,-1,0] - sample[:,-1,1], bin0, density=True)
  plots[i+1].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color=colors[i], line_color=colors[i], fill_alpha=0.2,line_alpha=0.)
  plots[i+1].step(bin_edges[:-1],hist, line_width=1, mode="after", color = colors[i], legend_label = tags[i])
  plots[i+1].title.text = labels[i]

bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[2]],
                                      [None, plots[3], plots[4]]]))

In [ ]:
#@title Phase plane visualization
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1
b = 1

Omega = 100 # 600

time_points = np.linspace(0, 20, 101)
population_0 = np.zeros(5, dtype=int)

# Parameters to analyze
args1 = (a, K, m, d, b*0, k, xi, th, g, Omega)
args2 = (a, K, m, d, b*3, k, xi, th, g, Omega)
args3 = (a, K, m, d, b*1, k, xi, th, g, Omega)

# Solving with Gillespie algorithm
samples1 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args1, n_threads=4,progress_bar=False)
samples2 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples3 = biocircuits.gillespie_ssa(simple_propensity_PF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples4 = biocircuits.gillespie_ssa(simple_propensity_NF_u2, simple_update, population_0,time_points, size=250, args=args3, n_threads=4,progress_bar=False)
samples5 = biocircuits.gillespie_ssa(simple_propensity_PF_u2, simple_update, population_0,time_points, size=250, args=args3, n_threads=4,progress_bar=False)

# Set up plots
fig_size = [300, 250] # to visualize
x_range = (0, 3)
y_range = (0, 3)

plots = []
for i in range(5):
    plots.append(bokeh.plotting.figure(width=fig_size[0], height=fig_size[1],
                          x_range=x_range,y_range=y_range, x_axis_label = 'y1', y_axis_label = 'y2'
                          ),)
    plots[i].axis.major_label_text_font_size = "10pt"     #background_fill_color="#fafafa"

y = np.linspace(0,8,800)

# Reference plot
y2_1, y2_2, u1 = Compute_IO(y, a, K, m, d, b*0, k, xi, th, g)
plots[0].line(y,y2_1,line_width=2, color="black", ) #
plots[0].line(y,y2_2,line_width=2, color="black", ) #

# Negative feedback with µ1 actuation
y2_1, y2_2, u1 = Compute_IO(y, a, K, m, d, b*3, k, xi, th, g)
plots[1].line(y,y2_1,line_width=2, color="black", ) #
plots[1].line(y,y2_2,line_width=2, color="black", ) #

# Positive feedback with µ1 actuation
y2_1, y1_2 = PF_null_u1(y, y, a, K, m, d, b*3, k, xi, th, g)
plots[2].line(y,y1_2,line_width=2, color="black", ) #
plots[2].line(y2_1,y,line_width=2, color="black", ) #

# Negative feedback with µ2 actuation
y1_2, y2_1 = NF_null_u2(y, y, a, K, m, d, b, k, xi, th, g)
plots[3].line(y, y1_2, line_width = 2, color = 'black',)
plots[3].line(y2_1, y, line_width = 2, color = 'black')

# Positive feedback with µ2 actuation
y2_2, y1_1 = Compute_IO_2_u2(y, a, K, m, d, b, k, xi, th, g)
y2_1 = Compute_IO_1_u2(y1_1, a, K, m, d, b, k, xi, th, g)
plots[4].line(y1_1, y2_1, line_width = 2, color = 'black',)
plots[4].line(y, y2_2, line_width = 2, color = 'black')

# Color coding according to steady-state value
for i in range(100):
    sol = samples1[i,:,:]/Omega
    ratio = sol[-1,0]/sol[-1,1]
    if ratio > 1:
        plots[0].line(sol[:,0],sol[:,1],line_width=1, color="blue",alpha= 0.1, line_join="bevel") #
    elif ratio < 1:
        plots[0].line(sol[:,0],sol[:,1],line_width=1, color="red",alpha= 0.1, line_join="bevel") #
    else:
        plots[0].line(sol[:,0],sol[:,1],line_width=1, color="black",alpha= 0.1, line_join="bevel") #
    plots[0].title.text = 'without controller'

    sol = samples2[i,:,:]/Omega
    ratio = sol[-1,0]/sol[-1,1]
    if ratio > 1:
        plots[1].line(sol[:,0],sol[:,1],line_width=1, color="blue",alpha= 0.1, line_join="bevel") #
    elif ratio < 1:
        plots[1].line(sol[:,0],sol[:,1],line_width=1, color="red",alpha= 0.1, line_join="bevel") #
    else:
        plots[1].line(sol[:,0],sol[:,1],line_width=1, color="black",alpha= 0.1, line_join="bevel") #
    plots[1].title.text = 'Negative feedback with µ1 actuation'

    sol = samples3[i,:,:]/Omega
    ratio = sol[-1,0]/sol[-1,1]
    if ratio > 1:
        plots[2].line(sol[:,0],sol[:,1],line_width=1, color="blue",alpha= 0.1, line_join="bevel") #
    elif ratio < 1:
        plots[2].line(sol[:,0],sol[:,1],line_width=1, color="red",alpha= 0.1, line_join="bevel") #
    else:
        plots[2].line(sol[:,0],sol[:,1],line_width=1, color="black",alpha= 0.1, line_join="bevel") #
    plots[2].title.text = 'Positive feedback with µ1 actuation'

    sol = samples4[i,:,:]/Omega
    ratio = sol[-1,0]/sol[-1,1]
    if ratio > 1:
        plots[3].line(sol[:,0],sol[:,1],line_width=1, color="blue",alpha= 0.1, line_join="bevel") #
    elif ratio < 1:
        plots[3].line(sol[:,0],sol[:,1],line_width=1, color="red",alpha= 0.1, line_join="bevel") #
    else:
        plots[3].line(sol[:,0],sol[:,1],line_width=1, color="black",alpha= 0.1, line_join="bevel") #
    plots[3].title.text = 'Negative feedback with µ2 actuation'

    sol = samples5[i,:,:]/Omega
    ratio = sol[-1,0]/sol[-1,1]
    if ratio > 1:
        plots[4].line(sol[:,0],sol[:,1],line_width=1, color="blue",alpha= 0.1, line_join="bevel") #
    elif ratio < 1:
        plots[4].line(sol[:,0],sol[:,1],line_width=1, color="red",alpha= 0.1, line_join="bevel") #
    else:
        plots[4].line(sol[:,0],sol[:,1],line_width=1, color="black",alpha= 0.1, line_join="bevel") #
    plots[4].title.text = 'Positive feedback with µ2 actuation'

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[2]],
                                      [None, plots[3], plots[4]]]))

<ipython-input-7-40c419eb82ce>:34: RuntimeWarning: divide by zero encountered in divide
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m) # (1) Eq y1(y2) (hill + b*u1) / d
<ipython-input-7-40c419eb82ce>:34: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m) # (1) Eq y1(y2) (hill + b*u1) / d
<ipython-input-8-aa2d7cc3d0d2>:65: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)


In [ ]:
#@title How does each architecture alter the equilibrium landscape?
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
b = 2
th = d
xi = 1
gv = (10,100,1000)
lim = 6

vec = np.linspace(0,5,7)

palette = bokeh.palettes.grey(5)[::-1]

# Set up plots
fig_size = [320, 225] # to visualize

plots = []
for i in range(8):
    plots.append(bokeh.plotting.figure(width=fig_size[0], height=fig_size[1],
                                       x_axis_label = 'β',
                                      #x_range=x_range,y_range=y_range,
                          ),)
    plots[i].axis.major_label_text_font_size = "10pt"

# Negative feedback
y1_1 = np.linspace(0,3,300)
y2_2 = np.linspace(0,3,300)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, bi in enumerate(vec):
        y1_2, y2_1 = NF_null_u2(y1_1, y2_2, a, K, m, d, bi, k, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y1_2, y2_1, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[0].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[0].circle(vec,out1[1,:],line_width=1, size = 7, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[0].circle(vec,out1[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

    plots[1].line(vec,out2[0,:],line_width=2, color=palette[kk+1], ) #
    plots[1].circle(vec,out2[1,:],line_width=1, size = 7, color=palette[kk+1], ) #
    plots[1].circle(vec,out2[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

plots[0].yaxis.axis_label = 'y1'
plots[1].yaxis.axis_label = 'y2'
plots[0].title.text = 'Negative feedback with µ2 actuation'
plots[0].x_range = Range1d(0, 5.1)
plots[1].x_range = Range1d(0, 5.1)

# Positive feedback
y1_2 = np.linspace(0,3,300)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, bi in enumerate(vec):
        y2_2, y1_1= Compute_IO_2_u2(y1_2, a, K, m, d, bi, k, xi, th, gi)
        y2_1 = Compute_IO_1_u2(y1_1, a, K, m, d, bi, k, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[2].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[2].circle(vec,out1[1,:],line_width=1, size = 7, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[2].circle(vec,out1[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

    plots[3].line(vec,out2[0,:],line_width=2, color=palette[kk+1], ) #
    plots[3].circle(vec,out2[1,:],line_width=1, size = 7, color=palette[kk+1], ) #
    plots[3].circle(vec,out2[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

plots[2].yaxis.axis_label = 'y1'
plots[3].yaxis.axis_label = 'y2'
plots[2].title.text = 'Positive feedback with µ2 actuation'
plots[2].x_range = Range1d(0,5.1)
plots[3].x_range = Range1d(0,5.1)

# Positive feedback
y1_1 = np.linspace(0,3,300)
y2_2 = np.linspace(0,3,300)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, bi in enumerate(vec):
        y1_2, y2_1 = PF_null_u1(y1_1, y2_2, a, K, m, d, bi, k, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y1_2, y2_1, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[4].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[4].circle(vec,out1[1,:],line_width=1, size = 7, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[4].circle(vec,out1[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

    plots[5].line(vec,out2[0,:],line_width=2, color=palette[kk+1], ) #
    plots[5].circle(vec,out2[1,:],line_width=1, size = 7, color=palette[kk+1], ) #
    plots[5].circle(vec,out2[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

plots[4].yaxis.axis_label = 'y1'
plots[5].yaxis.axis_label = 'y2'
plots[4].title.text = 'Positive feedback with µ1 actuation'
plots[4].x_range = Range1d(0, 5.1)
plots[5].x_range = Range1d(0, 5.1)

# Negative feedback
y1_2 = np.linspace(0,3,300)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, bi in enumerate(vec):
        y2_2, y1_1= Compute_IO_2(y1_2, a, K, m, d, bi, k, xi, th, gi)
        y2_1 = Compute_IO_1(y1_1, a, K, m, d, bi, k, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[6].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[6].circle(vec,out1[1,:],line_width=1, size = 7, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[6].circle(vec,out1[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

    plots[7].line(vec,out2[0,:],line_width=2, color=palette[kk+1], ) #
    plots[7].circle(vec,out2[1,:],line_width=1, size = 7, color=palette[kk+1], ) #
    plots[7].circle(vec,out2[2,:],line_width=1, size = 7, color=palette[kk+1],fill_color = 'white') #

plots[6].yaxis.axis_label = 'y1'
plots[7].yaxis.axis_label = 'y2'
plots[6].title.text = 'Negative feedback with µ1 actuation'
plots[6].x_range = Range1d(0,5.1)
plots[7].x_range = Range1d(0,5.1)

# Last details for plots
plots[0].y_range = Range1d(-0.1, 2.71)
plots[1].y_range = Range1d(0.5, 3.1)

plots[0].legend.location = 'bottom_left'
plots[0].legend.background_fill_alpha = 0.0

plots[2].y_range = Range1d(2.1, 2.5)
plots[3].y_range = Range1d(0, 2.5)

plots[2].legend.location = 'top_left'
plots[2].legend.background_fill_alpha = 0.0

plots[4].legend.location = 'bottom_left'
plots[4].legend.background_fill_alpha = 0.0

plots[6].legend.location = 'top_left'
plots[6].legend.background_fill_alpha = 0.0

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[4], plots[5]],
                                     [plots[2], plots[3], plots[6], plots[7]]]))

<ipython-input-15-aa2d7cc3d0d2>:65: RuntimeWarning: divide by zero encountered in divide
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
<ipython-input-15-aa2d7cc3d0d2>:65: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: divide by zero encountered in divide
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)


In [ ]:
#@title Comparing the negative and positive feedback with $u_1$ and $u_2$ actuations - Part 1
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1
b = 1

Omega = 100 # 600

time_points = np.linspace(0, 20, 101)
population_0 = np.zeros(5, dtype=int)

# Parameters to analyze

args1 = (a, K, m, d, b*0, k, xi, th, g, Omega)
args2 = (a, K, m, d, b*2, k, xi, th, g, Omega)

# Solving with Gillespie algorithm
samples1 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args1, n_threads=4,progress_bar=False)
samples2 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples3 = biocircuits.gillespie_ssa(simple_propensity_PF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples4 = biocircuits.gillespie_ssa(simple_propensity_NF_u2, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples5 = biocircuits.gillespie_ssa(simple_propensity_PF_u2, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)

# Visualization
plots = []
for i in range(5):
  plots.append(bokeh.plotting.figure(width = 280, height = 175,
                                     x_range = (-300, 300), y_range = (0, 0.02),
                                     x_axis_label = 'y1 - y2', y_axis_label = 'p'))
for i in range(5):
  plots.append(bokeh.plotting.figure(width = 280, height = 175,
                                     x_range = (0, 3.1), y_range = (0, 3.1),
                                     x_axis_label = 'y1', y_axis_label = 'y2'))
# Reference plot (histogram)
bin0 = np.arange(-3*Omega,3*Omega+6,8) #8
hist, bin_edges = np.histogram(samples1[:,-1,0] - samples1[:,-1,1], bin0, density=True)

plots[0].title.text = 'without controller'

for i in range(5):
  plots[i].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color="grey", line_color="grey", fill_alpha=0.2,line_alpha=0.)
  plots[i].step(bin_edges[:-1],hist, line_width=1, mode="after", color = "grey", legend_label = 'β = 0')
  plots[i].legend.location = 'top'
  plots[i].legend.background_fill_alpha = 0.0

# Reference plot (nulcliness)
y1_2 = np.logspace(-5,1,500)
y2_2, y1_1 = Compute_IO_2(y1_2, a, K, m, d, b*0, k, xi, th, g)
y2_1 = Compute_IO_1(y1_1, a, K, m, d, b*0, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[5].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[5].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[5].circle(y1_i, y2_i, size = 6, color = 'grey')

# IFFL controller (histogram)
sample_vec = [samples2, samples3, samples4, samples5]
colors = ['orange', 'blue', 'purple', 'green']
labels = ['Negative feedback with µ1 actuation', 'Positive feedback with µ1 actuation',
          'Negative feedback with µ2 actuation', 'Positive feedback with µ2 actuation',]

for i, sample in enumerate(sample_vec):
  hist, bin_edges = np.histogram(sample[:,-1,0] - sample[:,-1,1], bin0, density=True)
  plots[i+1].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color=colors[i], line_color=colors[i], fill_alpha=0.2,line_alpha=0.)
  plots[i+1].step(bin_edges[:-1],hist, line_width=1, mode="after", color = colors[i], legend_label = 'β = 1')
  plots[i+1].title.text = labels[i]

# Negative feedback with µ1 actuation
y2_2, y1_1 = Compute_IO_2(y1_2, a, K, m, d, b, k, xi, th, g)
y2_1 = Compute_IO_1(y1_1, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[6].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[6].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[6].circle(y1_i, y2_i, size = 6, color = colors[0])

# Positive feedback with µ1 actuation
y1_1 = np.logspace(-5,1,500)
y2_2 = np.logspace(-5,1,500)
y2_1, y1_2 = PF_null_u1(y1_1, y2_2, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[7].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[7].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[7].circle(y1_i, y2_i, size = 6, color = colors[1])

# Negative feedback with µ2 actuation
y1_1 = np.logspace(-5,1,500)
y2_2 = np.logspace(-5,1,500)
y1_2, y2_1 = NF_null_u2(y1_1, y2_2, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[8].line(y1_1, y2_1, line_width = 2, color = 'black', alpha = 0.4)
plots[8].line(y1_2, y2_2, line_width = 2, color = 'black', alpha = 0.4)
plots[8].circle(y1_i, y2_i, size = 6, color = colors[2])

# Positive feedback with µ2 actuation
y1_2 = np.logspace(-5,1,500)
y2_2, y1_1 = Compute_IO_2_u2(y1_2, a, K, m, d, b, k, xi, th, g)
y2_1 = Compute_IO_1_u2(y1_1, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[9].line(y1_1, y2_1, line_width = 2, color = 'black',alpha = 0.4)
plots[9].line(y1_2, y2_2, line_width = 2, color = 'black',alpha = 0.4)
plots[9].circle(y1_i, y2_i, size = 6, color = colors[3])

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[2], plots[3], plots[4]],
                                      [plots[5], plots[6], plots[7], plots[8], plots[9]]]))

<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: divide by zero encountered in divide
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
<ipython-input-15-aa2d7cc3d0d2>:65: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)


In [ ]:
#@title How much can we deviate from the derivative condition?
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1
b = 1

gv = (10,100,1000)
lim = 6

k_vec = np.linspace(0.5,2,7)
vec = d*xi/th/k_vec

palette = bokeh.palettes.grey(5)[::-1]

# Set up plots
fig_size = [320, 225] # to visualize
x_range = (0.4, 2.1)
y_range = (2.1, 2.51)

# Negative feedback with µ2 actuation
y1_1 = np.linspace(0,8,800)
y2_2 = np.linspace(0,8,800)

plots = []
for i in range(8):
    plots.append(bokeh.plotting.figure(width=fig_size[0], height=fig_size[1],
                          x_range=x_range,y_range=y_range
                          ),)
    plots[i].axis.major_label_text_font_size = "10pt"     #background_fill_color="#fafafa"

# Negative feedback with µ2 actuation
for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, ki in enumerate(k_vec):
        y1_2, y2_1 = NF_null_u2(y1_1, y2_2, a, K, m, d, b, ki, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[0].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[0].circle(vec,out1[1,:],line_width=1, size = 6, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[0].circle(vec,out1[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

    plots[1].line(vec,out2[0,:],line_width=2, color=palette[kk+1],) #
    plots[1].circle(vec,out2[1,:],line_width=1, size = 6, color=palette[kk+1],) #
    plots[1].circle(vec,out2[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

# Positive feedback with µ2 actuation
y1_2 = np.linspace(0,8,800)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, ki in enumerate(k_vec):
        y2_2, y1_1 = Compute_IO_2_u2(y1_2, a, K, m, d, b, ki, xi, th, gi)
        y2_1 = Compute_IO_1_u2(y1_1, a, K, m, d, b, ki, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[2].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[2].circle(vec,out1[1,:],line_width=1, size = 6, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[2].circle(vec,out1[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

    plots[3].line(vec,out2[0,:],line_width=2, color=palette[kk+1],) #
    plots[3].circle(vec,out2[1,:],line_width=1, size = 6, color=palette[kk+1],) #
    plots[3].circle(vec,out2[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

# Positive feedback with µ1 actuation
y1_1 = np.linspace(0,8,800)
y2_2 = np.linspace(0,8,800)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, ki in enumerate(k_vec):
        y1_2, y2_1 = PF_null_u1(y1_1, y2_2, a, K, m, d, b, ki, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[4].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[4].circle(vec,out1[1,:],line_width=1, size = 6, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[4].circle(vec,out1[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

    plots[5].line(vec,out2[0,:],line_width=2, color=palette[kk+1],) #
    plots[5].circle(vec,out2[1,:],line_width=1, size = 6, color=palette[kk+1],) #
    plots[5].circle(vec,out2[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

# Negative feedback with µ1 actuation
y1_2 = np.linspace(0,8,800)

for kk, gi in enumerate(gv):
    out1 = np.empty((3,len(vec),))*np.nan
    out2 = np.empty((3,len(vec),))*np.nan
    for i, ki in enumerate(k_vec):
        y2_2, y1_1 = Compute_IO_2(y1_2, a, K, m, d, b, ki, xi, th, gi)
        y2_1 = Compute_IO_1(y1_1, a, K, m, d, b, ki, xi, th, gi)
        y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)

        if len(y1_i)>0:
            out1[0,i] = np.max(y1_i)
            out2[0,i] = np.max(y2_i)
            if len(y1_i)==1:
                out1[2,i] = np.max(y1_i)
                out2[2,i] = np.max(y2_i)
            else:
                out1[1,i] = np.max(y1_i)
                out2[1,i] = np.max(y2_i)

    plots[6].line(vec,out1[0,:],line_width=2, color=palette[kk+1],) #
    plots[6].circle(vec,out1[1,:],line_width=1, size = 6, color=palette[kk+1], legend_label = f'{gi/g} γ ') #
    plots[6].circle(vec,out1[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

    plots[7].line(vec,out2[0,:],line_width=2, color=palette[kk+1],) #
    plots[7].circle(vec,out2[1,:],line_width=1, size = 6, color=palette[kk+1],) #
    plots[7].circle(vec,out2[2,:],line_width=1, size = 6, color=palette[kk+1],fill_color = 'white') #

# Last details for plots
for i in range(8):
  plots[i].xaxis.axis_label = 'r'
  if i % 2 == 0:
    plots[i].yaxis.axis_label  = 'y1'
    plots[i].legend.background_fill_alpha = 0.0
  else:
    plots[i].yaxis.axis_label  = 'y2'

plots[0].title.text = 'Negative feedback with µ2 actuation'
plots[2].title.text = 'Positive feedback with µ2 actuation'
plots[4].title.text = 'Positive feedback with µ1 actuation'
plots[6].title.text = 'Negative feedback with µ1 actuation'

plots[0].y_range = Range1d(0.5, 3.3)
plots[1].y_range = Range1d(1.8, 2.5)
plots[0].legend.location = 'bottom_left'

plots[2].y_range = Range1d(2.1, 2.4)
plots[3].y_range = Range1d(0, 2.5)
plots[2].legend.location = 'top_left'

plots[4].y_range = Range1d(2.1, 2.3)
plots[5].y_range = Range1d(2.1, 3.5)
plots[4].legend.location = 'top_right'

plots[6].y_range = Range1d(2.1, 2.4)
plots[7].y_range = Range1d(0., 2.3)
plots[6].legend.location = 'top_right'

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[4], plots[5]],
                                      [plots[2], plots[3], plots[6], plots[7]]]))

<ipython-input-15-aa2d7cc3d0d2>:65: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)


In [ ]:
#@title Comparing the negative and positive feedback with $u_1$ and $u_2$ actuation - Part 2
a = 2.2 # 2.2 alpha  uM/h
K = 1 # Kappa uM
m = 3 # 3 cooperatividad
d = 1 # delta 1/h
k = 1
g = 100
th = d
xi = 1.2
b = 2

Omega = 100 # 600

time_points = np.linspace(0, 20, 101)
population_0 = np.zeros(5, dtype=int)

# Parameters to analyze

args1 = (a, K, m, d, b*0, k, xi, th, g, Omega)
args2 = (a, K, m, d, b, k, xi, th, g, Omega)

# Solving with Gillespie algorithm
samples1 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args1, n_threads=4,progress_bar=False)
samples2 = biocircuits.gillespie_ssa(simple_propensity_NF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples3 = biocircuits.gillespie_ssa(simple_propensity_PF_u1, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples4 = biocircuits.gillespie_ssa(simple_propensity_NF_u2, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)
samples5 = biocircuits.gillespie_ssa(simple_propensity_PF_u2, simple_update, population_0,time_points, size=250, args=args2, n_threads=4,progress_bar=False)

# Visualization
plots = []
for i in range(5):
  plots.append(bokeh.plotting.figure(width = 280, height = 175,
                                     x_range = (-300, 300), y_range = (0, 0.02),
                                     x_axis_label = 'y1 - y2', y_axis_label = 'p'))
for i in range(5):
  plots.append(bokeh.plotting.figure(width = 280, height = 175,
                                     x_range = (0, 3.1), y_range = (0, 3.1),
                                     x_axis_label = 'y1', y_axis_label = 'y2'))
# Reference plot (histogram)
bin0 = np.arange(-3*Omega,3*Omega+6,8) #8
hist, bin_edges = np.histogram(samples1[:,-1,0] - samples1[:,-1,1], bin0, density=True)

plots[0].title.text = 'without controller'

for i in range(5):
  plots[i].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color="grey", line_color="grey", fill_alpha=0.2,line_alpha=0.)
  plots[i].step(bin_edges[:-1],hist, line_width=1, mode="after", color = "grey", legend_label = 'β = 0')
  plots[i].legend.location = 'top'
  plots[i].legend.background_fill_alpha = 0.0

# Reference plot (nulcliness)
y1_2 = np.logspace(-5,1,500)
y2_2, y1_1 = Compute_IO_2(y1_2, a, K, m, d, b*0, k, xi, th, g)
y2_1 = Compute_IO_1(y1_1, a, K, m, d, b*0, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[5].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[5].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[5].circle(y1_i, y2_i, size = 6, color = 'grey')

# IFFL controller (histogram)
sample_vec = [samples2, samples3, samples4, samples5]
colors = ['orange', 'blue', 'purple', 'green']
labels = ['Negative feedback with µ1 actuation', 'Positive feedback with µ1 actuation',
          'Negative feedback with µ2 actuation', 'Positive feedback with µ2 actuation',]

for i, sample in enumerate(sample_vec):
  hist, bin_edges = np.histogram(sample[:,-1,0] - sample[:,-1,1], bin0, density=True)
  plots[i+1].quad(top=hist, bottom=0, left=bin_edges[:-1], right=bin_edges[1:],fill_color=colors[i], line_color=colors[i], fill_alpha=0.2,line_alpha=0.)
  plots[i+1].step(bin_edges[:-1],hist, line_width=1, mode="after", color = colors[i], legend_label = 'β = 2')
  plots[i+1].title.text = labels[i]

# Negative feedback with µ1 actuation
y2_2, y1_1 = Compute_IO_2(y1_2, a, K, m, d, b, k, xi, th, g)
y2_1 = Compute_IO_1(y1_1, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[6].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[6].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[6].circle(y1_i, y2_i, size = 6, color = colors[0])

# Positive feedback with µ1 actuation
y1_1 = np.logspace(-5,1,500)
y2_2 = np.logspace(-5,1,500)
y2_1, y1_2 = PF_null_u1(y1_1, y2_2, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[7].line(y1_1,y2_1,line_width=2, color="black", alpha = 0.4) #
plots[7].line(y1_2,y2_2,line_width=2, color="black", alpha = 0.4) #
plots[7].circle(y1_i, y2_i, size = 6, color = colors[1])

# Negative feedback with µ2 actuation
y1_1 = np.logspace(-5,1,500)
y2_2 = np.logspace(-5,1,500)
y1_2, y2_1 = NF_null_u2(y1_1, y2_2, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[8].line(y1_1, y2_1, line_width = 2, color = 'black', alpha = 0.4)
plots[8].line(y1_2, y2_2, line_width = 2, color = 'black', alpha = 0.4)
plots[8].circle(y1_i, y2_i, size = 6, color = colors[2])

# Positive feedback with µ2 actuation
y1_2 = np.logspace(-5,1,500)
y2_2, y1_1 = Compute_IO_2_u2(y1_2, a, K, m, d, b, k, xi, th, g)
y2_1 = Compute_IO_1_u2(y1_1, a, K, m, d, b, k, xi, th, g)
y1_i, y2_i = intersection(y1_1, y2_1, y1_2, y2_2)
plots[9].line(y1_1, y2_1, line_width = 2, color = 'black', alpha = 0.4)
plots[9].line(y1_2, y2_2, line_width = 2, color = 'black', alpha = 0.4)
plots[9].circle(y1_i, y2_i, size = 6, color = colors[3])

# Visualization
bokeh.io.show(bokeh.layouts.gridplot([[plots[0], plots[1], plots[2], plots[3], plots[4]],
                                      [plots[5], plots[6], plots[7], plots[8], plots[9]]]))

<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: divide by zero encountered in divide
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
<ipython-input-14-40c419eb82ce>:68: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u1) - K**m)**(1/m)
<ipython-input-15-aa2d7cc3d0d2>:65: RuntimeWarning: invalid value encountered in power
  y2_1 = (a*K**m/(d*y - b*u2) - K**m)**(1/m)
